In [0]:
df_orders_silver = spark.read.parquet("/mnt/enterprise/silver/order_cleaned")
df_invoice_silver = spark.read.parquet("/mnt/enterprise/silver/invoice_cleaned")
df_sales_silver = spark.read.parquet("/mnt/enterprise/silver/sales_cleaned")


### DIM COMPANY

In [0]:
df_company = df_orders_silver.select("Company Id", "Company Name").distinct()


### DIM SALES REP

In [0]:
df_salesrep = df_sales_silver.select("Sales Rep Id", "Sales Rep").distinct()
                        

### DIM MEALS

In [0]:
df_meal = df_invoice_silver.select("Meal Id", "Type of Meal", "Meal Price").distinct() 

### DIM DATE

In [0]:
from pyspark.sql.functions import col, year, month, dayofmonth

df_dates = df_orders_silver.select(col("order_date").alias("date")) \
           .union(df_invoice_silver.select(col("Date").alias("date"))) \
           .distinct()

df_dim_date = df_dates.withColumn("year", year("date")) \
                      .withColumn("month", month("date")) \
                      .withColumn("day", dayofmonth("date"))


### WRITING TO GOLD FOLDER

In [0]:
df_company.write.mode("overwrite").parquet("/mnt/enterprise/gold/DimCompany")
df_salesrep.write.mode("overwrite").parquet("/mnt/enterprise/gold/DimSalesRep")
df_meal.write.mode("overwrite").parquet("/mnt/enterprise/gold/DimMeal")
df_dim_date.write.mode("overwrite").parquet("/mnt/enterprise/gold/DimDate")


In [0]:
print("SALES:", df_sales_silver.columns)
print("ORDERS:", df_orders_silver.columns)
print("INVOICE:", df_invoice_silver.columns)


SALES: ['Sales Rep', 'Sales Rep Id', 'Company Name', 'company_id']
ORDERS: ['order_id', 'company_id', 'Company Name', 'date', 'Order Value', 'Converted', 'order_date']
INVOICE: ['Order Id', 'Date', 'Meal Id', 'company_id', 'Date of Meal', 'Participants', 'Meal Price', 'Type of Meal']


### RENAMING COLUMNS TO KEEP THEM UNIFORM

In [0]:
# SALES
df_sales_silver = (
    df_sales_silver
    .withColumnRenamed("Order Id", "order_id")
    .withColumnRenamed("Company Id", "company_id")
)

# ORDERS
df_orders_silver = (
    df_orders_silver
    .withColumnRenamed("Order Id", "order_id")
    .withColumnRenamed("Company Id", "company_id")
    .withColumnRenamed("Meal Id", "meal_id")
)

# INVOICE
df_invoice_silver = (
    df_invoice_silver
    .withColumnRenamed("Sales Rep", "salesrep_name")
    .withColumnRenamed("Sales Rep Id", "salesrep_id")
    .withColumnRenamed("Company Id", "company_id")
)


In [0]:
df_invoice_silver = df_invoice_silver.withColumnRenamed("Order Id", "order_id")


In [0]:
df_sales_meal = df_orders_silver.join(
    df_invoice_silver,
    on=["order_id", "company_id"],
    how="left"
)

### FACT TABLE

In [0]:
df_fact = df_sales_meal.join(df_sales_silver, on="company_id", how="left")


In [0]:
df_fact_final = df_fact.select(
    "order_id","company_id",df_orders_silver["Company Name"].alias("Company Name"),"Order Value","Converted","order_date","meal Id","Meal Price","Type of Meal","Date of Meal","sales Rep Id","Sales Rep")

In [0]:
df_fact_final.write.mode("overwrite").parquet("/mnt/enterprise/gold/FactRetail")


In [0]:
display(df_fact_final)

order_id company_id Company Name Order Value Converted order_date meal Id Meal Price Type of Meal Date of Meal sales Rep Id Sales Rep 9WNXZMFWU3Z53L9K kkm6ezrn9w5nyxp6 Verbal Greenwich 5257 0 2018-03-17 null null null null 97UNNAT790E0WM4N Jessie Mcallister WJZ6EUGNG7SXIOIS 93du98kt3nzcow58 Victorian Aim 1345 0 2014-04-29 null null null null 97UNNAT790E0WM4N Jessie Mcallister D2H4LO1VHWPU3P8E uznnig9mb0ri0y1n Garish Bishopsgate 5515 0 2017-05-09 null null null null RRD2R9XMAJDP7TUY Lois Bowers SZXZYGHG34OXADGG 01w2dwjssyimc2cp State-Local Minstrel 8126 0 2018-06-02 null null null null VZV7I6YA8IAX510X Betty Factor T5NTUBE0IO4IX09Q 21g0lxkzmavpikbr Brown Ambiguities 8074 0 2016-07-21 8PLYLHAUI6YW10CQ 743 Dinner 2016-07-21T20:00:00.000+0000 SKF2FH8QYJVNMOEH Jeffrey Edwards WJ8S0ZSX0SBTILUK poz4ypqeaj1c3jhi Megakaryocytic Producer 896 0 2018-06-03 null null null null 7BHT6W2NBWQC5X8T Latesha Tessitore NZXSFJAQHQXWVM2I yyqufmdxmymrz6oo Drugless Hiss 7140 0 2014-08-21 null null null null 7BHT6W2NBWQC5X8T Latesha Tessitore P5IKTPGE09TFDHLG a6o0ijf9wxb6irun Non-Dissonant Building 4160 0 2018-02-17 03MEF4HQ7SIBH0HD 308 Breakfast 2018-02-17T07:00:00.000+0000 NCSC6S6XU5TJF3VC Billy Breece D4WCRLKIMQ23HH1D l0d1j5j3x9q6glya Approximate Cough 5073 0 2016-04-04 null null null null PUEODHWAR7PERPWP Cherry Phillips VTWO0TWW0292ZOBH cy34wwcbyf6pbwhu Snazzy Amendment 8876 0 2018-03-15 1MUKMJ3MBDWI10NL 666 Lunch 2018-03-17T12:00:00.000+0000 T2LBAPSG044EFXTT William Michel F4G14FW5LT76Q075 gvwxmk2nogxxdt67 Nonfunctional Gauze 4153 0 2018-01-17 null null null null T2LBAPSG044EFXTT William Michel BYQRDDKR28U2E7KW rnpyawlcaibswm8j Glutinous $30,000 1956 0 2018-07-19 null null null null T2LBAPSG044EFXTT William Michel 6WZHOFP225R0E62O se41oint8qi9gzhj Hundredth Sabella 1275 1 2015-08-17 3TQGYEB2P21PFV6F 94 Lunch 2015-08-15T12:00:00.000+0000 T2LBAPSG044EFXTT William Michel JFUPZRWAYA0FJ273 n40jggxvyswdnij9 Neurotic Pavilions 355 0 2016-05-04 VDTL6214632D5U4K 34 Breakfast 2016-05-06T07:00:00.000+0000 P33NCMUO2PX6Y6RT Derek Walters 3769GUK9PUK4TGS6 sxshvhnjhfrm803x Sor'L Planet'S 8512 0 2014-07-31 OE13XJLSUON7CYEP 604 Dinner 2014-08-01T19:00:00.000+0000 XKO58UE8J5784EY9 Michael Mackenzie GAIT9QHCSRX25MMB yeawaz79njgzqp9m Leaky Impresario 3340 0 2014-08-17 VP9H2XJMQ9CZ3DXV 247 Lunch 2014-08-17T10:00:00.000+0000 4LIPY9OFVGP86P27 Michael Means ABMI9B7J5DBDK1FC dmn9h2ue0oelcyw0 Mass-Building Nostradamus 2093 0 2017-11-09 21T90FOY99CV6LHM 159 Breakfast 2017-11-13T07:00:00.000+0000 JNC2O6MVEDL80P0D Melissa Reeves QCE5AM5PEIVDJY7L 3rgk4zitkh0ap3of Sandwich-Type Applicant 3854 0 2015-08-08 null null null null SK2BRT9HUQUWDID1 Wanda Carr N8YVQKS8KF72USUX rl2akvc5ljd1caie Ordinary Tenite 7396 0 2018-12-02 JRJZ1SAWQOIRJK20 584 Lunch 2018-12-06T13:00:00.000+0000 K7RF21RAURCXNFXC Kenneth Klinger 92MOMEFL4WT80YOG kledur54vzg5by24 Unkind Denominators 3850 1 2015-08-23 AW3GBAWZNQSDCXQZ 366 Breakfast 2015-08-19T07:00:00.000+0000 K7RF21RAURCXNFXC Kenneth Klinger PNAN4V5R95JJMFS0 06v2udb1s4mlsiam Unneeded Titters 7701 0 2014-04-15 WQDIPQ3XIMM40AUI 655 Lunch 2014-04-11T11:00:00.000+0000 LSLB91X9EV671OMJ Joshua Grant QUFHF7EK0BZ32TLR hteppex1rocfpehj Impulsive Copp 9967 0 2017-11-27 JOB4965IVZBY997D 837 Lunch 2017-11-30T13:00:00.000+0000 UMGYZWYAZKLBMPDO Denise Sanchez FSATI8JQ1Y96TZJK 2y14dxmrf9g28k2o Incoherent Corpulence 2468 0 2017-01-07 null null null null 3BG1V1LA09JIRV4J Jose Martinez 2UE54VDIQ3UI3ACU bylesiolw87hngd2 Universal Dillinger 2371 0 2015-01-19 PB8KW7JO22CKPKGU 190 Breakfast 2015-01-23T06:00:00.000+0000 S8ESJ4C56BV8LFSF Margaret Cohen 5JD2ZLO8J6BTEI2M 1lbqaxcdx4vrfepf 12-Month Origin 1890 0 2014-04-05 null null null null MBOOU4LRZUTJ9UUA Gregory Outen NSRCJH9APEI5PXD2 yxww7roz356qp9i8 Eighteenth- Sanctity 3554 0 2017-05-12 C137FACA7HDXVRP0 284 Dinner 2017-05-08T18:00:00.000+0000 UODO0E3FMQ6I8SVM Richard Castro VB056DO62Z6AGRBI qp7hb11sqktylu2u Effective Pavements 1998 0 2015-08-13 LWAKQ53W3DOXDDI5 136 Breakfast 2015-08-15T06:00:00.000+0000 3QH495WG1SI67FS6